This Notebook will take a Youtube Playlist and convert all videos to MP3:s , which will be stored on a folder on your Google Drive.

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
#@markdown Fixed yt-dlp downloader – works in December 2025 (real mp3 + thumbnails)
youtube_link = '' #@param {type:'string'}
playlist_start = 1 #@param {type:"number"}
playlist_end = 9999 #@param {type:"number"}

# 1. Install the absolute bleeding-edge yt-dlp (nightly) + modern Node.js 20
!pip install -U --force-reinstall --no-deps https://github.com/yt-dlp/yt-dlp-nightly-builds/releases/latest/download/yt-dlp.tar.gz -q
!wget -q https://nodejs.org/dist/v20.18.0/node-v20.18.0-linux-x64.tar.xz
!tar -xf node-v20.18.0-linux-x64.tar.xz
!cp node-v20.18.0-linux-x64/bin/node /usr/local/bin/node
!rm -v

# 2. Go to save folder
import os
%cd /content/drive/MyDrive/Saved from Chrome

# 3. Download (this combination finally beats the new n-challenge in Dec 2025)
!yt-dlp \
    --concurrent-fragments 16 \
    --retries 30 \
    --fragment-retries 30 \
    --extractor-retries 10 \
    --user-agent "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36" \
    --extractor-args "youtube:player_client=web;skip=initial_data" \
    --format "bestaudio/best" \
    --audio-format mp3 \
    --audio-quality 0 \
    --embed-thumbnail \
    --add-metadata \
    --playlist-start {playlist_start} \
    --playlist-end {playlist_end} \
    -o "%(title)s.%(ext)s" \
    {youtube_link}

In [ ]:
#@markdown Initialize ✅
#Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')

#Initialize
import os
def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)
my_mkdirs('/content/tmp/')

#
!python3 -m pip install --force-reinstall https://github.com/yt-dlp/yt-dlp/archive/master.tar.gz
import yt_dlp as youtube_dl

In [ ]:
# @markdown download video or playlist as audio file mp3
youtube_link = '' # @param {type:'string'}
playlist_start = 1
## @param {type:'number'}
playlist_end = 9999
## @param {type:'number'}

#Extract all videos in YT playlist mp3 files
#Aborting this code is fine if list is latge ( You will keep downloaded mp3:s)
%cd /content/drive/MyDrive/Saved from Chrome/
for playlist_URL in youtube_link.split(','):
  !yt-dlp --cookies /content/drive/MyDrive/ytcookies.txt --playlist-end {playlist_end} --playlist-start {playlist_start} --extract-audio --audio-format mp3 -o "%(title)s.%(ext)s" {playlist_URL}

In [ ]:

# @markdown Download video or playlist as highest video quality mp4
youtube_link = '' # @param {type:'string'}
playlist_start = 1
## @param {type:'number'}
playlist_end = 9999
## @param {type:'number'}

#Extract all videos in YT playlist mp3 files
#Aborting this code is fine if list is latge ( You will keep downloaded mp3:s)
%cd /content/drive/MyDrive/Saved from Chrome/
for playlist_URL in youtube_link.split(','):
  !yt-dlp --cookies /content/drive/MyDrive/ytcookies.txt --playlist-end {playlist_end} --playlist-start {playlist_start} --merge-output-format mp4 -f "bestvideo+bestaudio[ext=m4a]/best"  -o "%(title)s.%(ext)s" {playlist_URL}

In [ ]:

# @markdown 🌊 Rapid keyframe processing
# @markdown <br> ------ <br> Extract Keyframes from ALL mp4 / webm videos found on Google Drive
# @markdown <br> Be mindful of Google Drive Terms of Service
# @markdown <br> This cell will process all mp4 videos found under
# @markdown <br> /content/drive/MyDrive/Saved from Chrome/
delete_mp4_when_done = True # @param {type:'boolean'}
# @markdown <br> deleted mp4/webm files will be found under 'trash' in your Google drive
# @markdown <br> -------
# @markdown <br>  (Optional) Add a direct video link to below field.
# @markdown <br>  Multiple links can be written in this field
# @markdown <br> separated by comma.  Like this: <br> ' https:\\\my_video.mp4  ,  https:\\\second_video.webm ,  ....  '
import os
import shutil
!pip install video-kf
!pip install ffmpeg-python
!pip install wget
!pip install moviepy
import wget
import videokf as vf
import time
proc_keyframes=True # @param {type:'boolean'}
proc_audio=False # @param {type:'boolean'}
#def mkdirs(folder):
#  if not os.path.exists(folder):os.makedirs(folder)
#----#
direct_link = '' # @param {type:'string'}
# @markdown The linked videos will be downloaded to the Google drive prior to running the script.
# @markdown <br> This feature is useful for direct processing .webm from 4chan threads into keyframes
use_link = False # @param {type:'boolean'}
if direct_link.find('http')>-1: use_link = True
if use_link:
  %cd '/content/drive/MyDrive/Saved from Chrome/'
  for link in direct_link.split(','):
    if not link.find('http')>-1:continue
    wget.download(link.strip())
    time.sleep(5)
  %cd '/content/'
#-----#
filenames = []
srcpath = '/content/drive/MyDrive/Saved from Chrome/'
destpath = '/content/drive/MyDrive/'
localpath = '/content/'
converted = ''
for filename in os.listdir(f'{srcpath}'):
  if filename.find('.zip')>-1:
    %cd {srcpath}
    !unzip {filename}
    os.remove(filename)
    filename = filename.replace('.zip','')
  for suffix in ['.mkv','.mp4','.webm']:
    if filename.find(f'{suffix}')>-1: filenames.append(filename)
#Rename the downloaded video to 'tgt0' before running this cell
def my_mkdirs(folder):
  if os.path.exists(folder):shutil.rmtree(folder)
  os.makedirs(folder)
#----#
# @markdown Write a funny name for the folder(s) containing the keyframes
name_keyframes_as='' # @param {type:'string'}
# @markdown Created .zip files will not be overwritten
#NUM_ITEMS = 1 # @param {type:'slider', min:1 , max:20,step:1}
if name_keyframes_as.strip()=='': name_keyframes_as='keyframes'
num = 0
savepath = ''
%cd {localpath}
for filename in filenames:
  tgt_folder = f'/content/tmp'
  my_mkdirs(f'{tgt_folder}')
  print(f'Now processing video {filename}...')
  if proc_keyframes:
    vf.extract_keyframes(f'{srcpath}{filename}',output_dir_keyframes=f'{tgt_folder}')
    savepath = f'{destpath}{name_keyframes_as}_v{num}_kf'
    #---#
    while os.path.exists(f'{savepath}.zip'):
      #print(f'{savepath}.zip already exists...')
      num = num+1
      savepath = f'{destpath}{name_keyframes_as}_v{num}_kf'
    #---#
    shutil.make_archive(savepath,'zip' , f'{tgt_folder}')
    #from moviepy.editor import VideoFileClip
  if proc_audio:
    from moviepy.editor import VideoFileClip
    # Load the WebM file
    video = VideoFileClip(f"{srcpath}{filename}")

    # Extract audio and save as MP3 (or WAV, etc.)
    audio = video.audio
    savepath = f"{destpath}_audio_v{num}.mp3"

    while os.path.exists(savepath):
      num = num+1
      savepath= f"{destpath}_audio_v{num}.mp3"
    #----#
    if audio:
      audio.write_audiofile(f'{savepath}')
      # Close the files to free resources
      audio.close()
      video.close()
  #----#
  if delete_mp4_when_done: os.remove(f'{srcpath}{filename}')
  num = num+1


In [ ]:
import os
import zipfile
import glob
from google.colab import drive
import shutil
from pathlib import Path

# Mount Google Drive
drive.mount('/content/drive')

# Define the directory containing the zip files
zip_dir = '/content/drive/MyDrive/'
zip_pattern = 'keyframes_v*_kf.zip'
output_zip = '/content/drive/MyDrive/all_keyframes_combined.zip'

# Temporary extraction directory
temp_dir = '/content/temp_extracted'
os.makedirs(temp_dir, exist_ok=True)

# Function to check if file is an image
def is_image_file(filename):
    image_extensions = {
        '.jpg', '.jpeg', '.png', '.gif', '.bmp', '.tiff', '.tif',
        '.webp', '.ico', '.svg', '.heic', '.heif', '.raw', '.cr2',
        '.nef', '.arw', '.dng', '.jpe', '.jp2', '.j2k'
    }
    ext = Path(filename).suffix.lower()
    return ext in image_extensions

# Store original zip files for cleanup
original_zip_files = []

print("Finding zip files...")
zip_files = glob.glob(os.path.join(zip_dir, zip_pattern))
original_zip_files = zip_files.copy()  # Keep for cleanup
print(f"Found {len(zip_files)} zip files: {[os.path.basename(z) for z in zip_files]}")

# Extract each zip file
image_txt_pairs = []
for zip_path in zip_files:
    print(f"\n🔓 Extracting: {os.path.basename(zip_path)}")

    with zipfile.ZipFile(zip_path, 'r') as zip_ref:
        # Extract to temporary directory with unique subfolder
        unique_subdir = os.path.join(temp_dir, Path(zip_path).stem)
        zip_ref.extractall(unique_subdir)

        # Find all files in the extracted content
        for root, dirs, files in os.walk(unique_subdir):
            for file in files:
                file_path = os.path.join(root, file)
                base_name = Path(file).stem
                ext = Path(file).suffix.lower()

                if is_image_file(file):
                    # Look for corresponding txt file
                    txt_path = None
                    possible_txt_names = [
                        f"{base_name}.txt",
                        f"{base_name.lower()}.txt",
                        f"{base_name.upper()}.txt"
                    ]

                    for txt_name in possible_txt_names:
                        potential_txt = os.path.join(root, txt_name)
                        if os.path.exists(potential_txt):
                            txt_path = potential_txt
                            break

                    image_txt_pairs.append({
                        'image_path': file_path,
                        'txt_path': txt_path,
                        'base_name': base_name
                    })

print(f"\n📊 Total image-txt pairs found: {len(image_txt_pairs)}")
print(f"   Images with matching txt: {sum(1 for p in image_txt_pairs if p['txt_path'])}")
print(f"   Images without txt: {sum(1 for p in image_txt_pairs if not p['txt_path'])}")

# Create the output zip file
print("\n🗜️ Creating combined zip file...")
combined_zip_created = False

try:
    with zipfile.ZipFile(output_zip, 'w', zipfile.ZIP_DEFLATED) as output_zip_file:
        for i, pair in enumerate(image_txt_pairs, 1):
            try:
                # Create new image filename (keep original extension)
                original_ext = Path(pair['image_path']).suffix.lower()
                new_image_name = f"{i}{original_ext}"

                # Add image
                with open(pair['image_path'], 'rb') as img_file:
                    img_data = img_file.read()
                output_zip_file.writestr(new_image_name, img_data)

                # Add corresponding txt file if exists
                if pair['txt_path'] and os.path.exists(pair['txt_path']):
                    new_txt_name = f"{i}.txt"
                    with open(pair['txt_path'], 'rb') as txt_file:
                        txt_data = txt_file.read()
                    output_zip_file.writestr(new_txt_name, txt_data)

                if i % 50 == 0:
                    print(f"Processed {i}/{len(image_txt_pairs)} items...")

            except Exception as e:
                print(f"❌ Error processing item {i}: {e}")
                continue

    # Verify the output zip was created successfully
    if os.path.exists(output_zip) and os.path.getsize(output_zip) > 0:
        combined_zip_created = True
        print("✅ Combined zip file created successfully!")
    else:
        print("❌ Failed to create combined zip file!")
        combined_zip_created = False

except Exception as e:
    print(f"❌ Error creating combined zip: {e}")
    combined_zip_created = False

# Clean up temporary directory
try:
    shutil.rmtree(temp_dir, ignore_errors=True)
    print("🧹 Temporary extraction files cleaned up")
except:
    print("⚠️ Could not clean up temporary extraction files")

# Remove original zip files ONLY if combined zip was created successfully
if combined_zip_created and original_zip_files:
    print(f"\n🗑️ Removing {len(original_zip_files)} original zip files...")
    removed_count = 0

    for zip_path in original_zip_files:
        try:
            if os.path.exists(zip_path):
                os.remove(zip_path)
                print(f"   🗑️ Removed: {os.path.basename(zip_path)}")
                removed_count += 1
            else:
                print(f"   ⚠️ File not found: {os.path.basename(zip_path)}")
        except Exception as e:
            print(f"   ❌ Failed to remove {os.path.basename(zip_path)}: {e}")

    print(f"✅ Successfully removed {removed_count}/{len(original_zip_files)} original zip files")
else:
    print("\n⚠️ Skipping removal of original files - combined zip creation failed!")
    print("   Original files preserved for safety.")

# Final verification
if os.path.exists(output_zip):
    with zipfile.ZipFile(output_zip, 'r') as z:
        file_list = z.namelist()
        print(f"\n🔍 Final verification:")
        print(f"   📁 Combined zip: {output_zip}")
        print(f"   📊 Total files: {len(file_list)}")

        images_count = len([f for f in file_list if is_image_file(f)])
        txts_count = len([f for f in file_list if f.endswith('.txt')])
        print(f"   🖼️ Images: {images_count}")
        print(f"   📄 Text files: {txts_count}")

        # Check for matching pairs
        image_numbers = set()
        txt_numbers = set()
        for f in file_list:
            if is_image_file(f):
                try:
                    num = int(Path(f).stem)
                    image_numbers.add(num)
                except:
                    pass
            elif f.endswith('.txt'):
                try:
                    num = int(Path(f).stem)
                    txt_numbers.add(num)
                except:
                    pass

        matched_pairs = len(image_numbers & txt_numbers)
        print(f"   🔗 Matched image-txt pairs: {matched_pairs}")
        print(f"   💾 Size: {os.path.getsize(output_zip) / (1024*1024):.1f} MB")

print(f"\n🎉 Process completed!")
print(f"📁 Final output: {output_zip}")
if combined_zip_created:
    print("✅ All original zip files have been removed.")
else:
    print("⚠️ Original files preserved due to error.")

In [ ]:
# @title YouTube Channel → ALL Thumbnails (force tabs) → ZIP
# @markdown Paste **one or more** YouTube URLs (video, playlist **or channel**).
# @markdown Separate several links with a comma.

!pip install --quiet --force-reinstall https://github.com/yt-dlp/yt-dlp/archive/master.tar.gz
import yt_dlp as youtube_dl
import os, re, shutil, time
from google.colab import drive
from tqdm.auto import tqdm

drive.mount('/content/drive', force_remount=False)

# ---------- USER PARAMETERS ----------
youtube_links = ''  # @param {type:"string"}
zip_filename  = 'yt_thumbs'                                                # @param {type:"string"}
max_thumbs    = 501                                                        # @param {type:"slider", min:1, max:2000, step:10}

# ---------- PATHS ----------
SAVE_DIR  = '/content/drive/MyDrive/Saved from Chrome'
TEMP_DIR  = '/content/yt_thumbs_temp'
os.makedirs(TEMP_DIR, exist_ok=True)

# clean previous run
for f in os.listdir(TEMP_DIR):
    os.remove(os.path.join(TEMP_DIR, f))

ZIP_PATH = os.path.join(SAVE_DIR,
                        re.sub(r'[<>:"/\\|?*]', '_', zip_filename.strip() or 'yt_thumbs') + '.zip')

# ---------- yt-dlp base options ----------
BASE_OPTS = {
    'quiet'        : True,
    'no_warnings'  : True,
    'skip_download': True,
    # 'cookiefile'   : '/content/drive/MyDrive/ytcookies.txt'   # <-- uncomment if you have cookies
}

# ---------- Helpers ----------
def sanitize(name: str) -> str:
    return re.sub(r'[<>:"/\\|?*]', '_', name)[:180]

def download_thumb(info: dict) -> bool:
    thumbs = info.get('thumbnails') or []
    if not thumbs: return False
    best = max(thumbs, key=lambda t: (t.get('width') or 0)*(t.get('height') or 0))
    url  = best['url']
    ext  = url.split('?')[0].split('.')[-1]
    if ext not in {'jpg','jpeg','png','webp'}: ext = 'jpg'
    title = info.get('title') or info.get('id', 'unknown')
    fname = f"{sanitize(title)}.{ext}"
    fpath = os.path.join(TEMP_DIR, fname)
    !curl -s -L -o "{fpath}" "{url}"
    return os.path.exists(fpath)

def collect_from_playlist(url: str, collected: list, limit: int):
    """Recursively collect *video* entries from a playlist/tab."""
    if len(collected) >= limit: return
    ydl = youtube_dl.YoutubeDL({**BASE_OPTS, 'extract_flat': False})
    try:
        info = ydl.extract_info(url, download=False)
    except Exception as e:
        print(f"  [Warning] Failed {url}: {e}")
        return

    # single video
    if info.get('_type') in ('video', None) or 'entries' not in info:
        if len(collected) < limit:
            collected.append(info)
        return

    # playlist → walk entries
    for entry in info.get('entries', []):
        if entry is None: continue
        if entry.get('_type') == 'playlist' and entry.get('url'):
            sub = entry['url']
            if not sub.startswith('http'): sub = f"https://www.youtube.com{sub}"
            collect_from_playlist(sub, collected, limit)
        else:
            if len(collected) < limit:
                collected.append(entry)

# ---------- MAIN ----------
urls = [u.strip() for u in youtube_links.split(',') if u.strip()]
if not urls:
    raise ValueError("Please fill **youtube_links** with at least one URL.")

video_infos = []

for raw in urls:
    print(f"\nScanning: {raw}")

    # ---- 1. Detect channel -------------------------------------------------
    is_channel = any(p in raw for p in ['/@', '/c/', '/user/', '/channel/'])
    base_url   = raw.split('?')[0].rstrip('/')

    tab_suffixes = ['/videos', '/shorts', '/streams', '/playlists']
    tab_urls     = [base_url + s for s in tab_suffixes]

    if is_channel:
        print(f"  [Info] Forcing {len(tab_urls)} tabs: {tab_suffixes}")
        for tab in tab_urls:
            print(f"    → {tab}")
            collect_from_playlist(tab, video_infos, max_thumbs)
            if len(video_infos) >= max_thumbs: break
    else:
        # normal video / playlist
        collect_from_playlist(raw, video_infos, max_thumbs)

    if len(video_infos) >= max_thumbs: break

print(f"\nCollected {len(video_infos)} video entries (limit {max_thumbs}).")
if not video_infos:
    print("No videos found – check the channel URL or try a different tab.")
else:
    print("Downloading thumbnails …")
    pbar = tqdm(total=len(video_infos), desc="Thumbs", unit="thumb")
    downloaded = 0
    for info in video_infos:
        if download_thumb(info): downloaded += 1
        pbar.update(1)
    pbar.close()
    print(f"\nDownloaded {downloaded}/{len(video_infos)} thumbnails.")

    print("Creating ZIP …")
    shutil.make_archive(ZIP_PATH.replace('.zip', ''), 'zip', TEMP_DIR)
    print(f"ZIP ready → {ZIP_PATH}")

# clean temp folder
shutil.rmtree(TEMP_DIR)

In [ ]:
# Google Colab code to download the video from the given embed URL and save it to Google Drive
#@markdown Try a non-YT url
url ='' #@param{type:'string'}
# Step 1: Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')

# Step 2: Install yt-dlp (a powerful video downloader that supports TXXX.com)
!pip install -U yt-dlp

# Step 3: Download the video directly to your Google Drive
# The video will be saved in your Drive's root folder (My Drive). You can change the path if needed.

# Optional: For best quality (if multiple formats are available)
!yt-dlp {url} -o "/content/drive/MyDrive/Saved from Chrome/%(title)s.%(ext)s"

print("Download complete! Check your Google Drive.")

Auto-Disconnect From Drive ⬇️

In [ ]:
from google.colab import runtime
runtime.unassign()


